In [23]:
spark.stop()

In [80]:
from pyspark.sql import SQLContext
from pyspark import SparkContext
from pyspark.sql.types import *

from sparknlp.base import *
from sparknlp.pretrained import PretrainedPipeline
import sparknlp
from pyspark.sql import SparkSession
#sc = SparkContext()
import sparknlp
spark = sparknlp.start()

'''
spark = SparkSession.builder \
    .appName(" ")\
    .master("local[*]")\
    .config("spark.driver.memory","8G")\
    .config("spark.driver.maxResultSize", "2G")\
    .config("spark.jar", "/home/yogender/sparknlp.jar")\
    .config("spark.driver.extraClassPath", "/home/yogender/sparknlp.jar")\
    .config("spark.executor.extraClassPath", "/home/yogender/sparknlp.jar")\
    .config("spark.kryoserializer.buffer.max", "500m")\
    .getOrCreate()
'''

'\nspark = SparkSession.builder     .appName(" ")    .master("local[*]")    .config("spark.driver.memory","8G")    .config("spark.driver.maxResultSize", "2G")    .config("spark.jar", "/home/yogender/sparknlp.jar")    .config("spark.driver.extraClassPath", "/home/yogender/sparknlp.jar")    .config("spark.executor.extraClassPath", "/home/yogender/sparknlp.jar")    .config("spark.kryoserializer.buffer.max", "500m")    .getOrCreate()\n'

In [81]:
sqlContext = SQLContext(spark)

/home/yogender/.local/lib/python3.6/site-packages/pyspark/sql/context.py:79: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  FutureWarning


In [82]:
rdd_l = spark.sparkContext.wholeTextFiles("./*.html")

In [87]:
header = '<meta itemprop="currency" content="CZK">'
#rdd2 = rdd_l.map(lambda x: x[1]).map(lambda x: x.split(','))
#df = rdd2.toDF().show()
df = rdd_l.toDF(schema=["filename", "text"]).select("text")
#df.show()

In [91]:
df.show()

+--------------------+
|                text|
+--------------------+
|<!DOCTYPE html><h...|
+--------------------+
only showing top 1 row



TypeError: 'NoneType' object is not subscriptable

In [27]:
text = """
<div id="theworldsgreatest" class='my-right my-hide-small my-wide toptext' style="font-family:'Segoe UI',Arial,sans-serif">
    THE WORLD'S LARGEST WEB DEVELOPER SITE
    <h1 style="font-size:300%;">THE WORLD'S LARGEST WEB DEVELOPER SITE</h1>
    <p style="font-size:160%;">Lorem Ipsum is simply dummy text of the printing and typesetting industry. Lorem Ipsum has been the industry's standard dummy text ever since the 1500s, when an unknown printer took a galley of type and scrambled it to make a type specimen book. It has survived not only five centuries, but also the leap into electronic typesetting, remaining essentially unchanged. It was popularised in the 1960s with the release of Letraset sheets containing Lorem Ipsum passages, and more recently with desktop publishing software like Aldus PageMaker including versions of Lorem Ipsum..</p>
</div>
</div>"""

In [92]:
#df = spark.createDataFrame([[text]]).toDF("text").show(1)

+--------------------+
|                text|
+--------------------+
|\n<div id="thewor...|
+--------------------+



In [93]:
action = "extract"
tag = 'name'
patterns = [tag]

In [29]:
import sparknlp
from sparknlp.base import *
from sparknlp.annotator import *
from pyspark.ml import Pipeline

documentAssembler = DocumentAssembler() \
    .setInputCol('text') \
    .setOutputCol('document')

cleanUpPatterns = ["<div[^>]></p></div></div>"]

documentNormalizer = DocumentNormalizer() \
    .setInputCols("document") \
    .setOutputCol("normalizedDocument") \
    .setAction("clean") \
    .setPatterns(cleanUpPatterns) \
    .setReplacement(" ") \
    .setPolicy("pretty_all") \
    .setLowercase(True)


In [30]:
documentAssembler = DocumentAssembler() \
    .setInputCol("text") \
    .setOutputCol("document")
cleanUpPatterns = ["<[^>]>"]
documentNormalizer = DocumentNormalizer() \
    .setInputCols("document") \
    .setOutputCol("normalizedDocument") \
    .setAction("clean") \
    .setPatterns(cleanUpPatterns) \
    .setReplacement(" ") \
    .setPolicy("pretty_all") \
    .setLowercase(True)


In [31]:
docPatternRemoverPipeline = \
  Pipeline() \
    .setStages([
        documentAssembler,
        documentNormalizer
    ])


In [32]:
#data = spark.createDataFrame([[text]]).toDF("text")
#ds = docPatternRemoverPipeline.fit(data).transform(data)


In [33]:
ds = docPatternRemoverPipeline.fit(df).transform(df)


In [13]:
ds.selectExpr("normalizedDocument.result").show(truncate=False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [14]:
ds.select("normalizedDocument").show(10, False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [77]:
import sparknlp
from sparknlp.base import *
from sparknlp.annotator import *
from pyspark.ml import Pipeline
documentAssembler = DocumentAssembler() \
    .setInputCol("text") \
    .setOutputCol("document")
cleanUpPatterns = ["(?U)<[^>]><-->"]
pattern = "\\s+|(?=[-.:;*+,$&%\\[\\]])|(?<=[-.:;*+,$&%\\[\\]])"
#patterns = ["([^.@\\s]+)(\\.[^.@\\s]+)*@([^.@\\s]+\\.)+([^.@\\s]+)"]
documentNormalizer = DocumentNormalizer() \
    .setInputCols("document") \
    .setOutputCol("normalizedDocument") \
    .setAction("clean") \
    .setPatterns(patterns) \
    .setReplacement("@") \
    .setPolicy("pretty_all") \
    .setLowercase(True)

sentenceDetector = SentenceDetector()\
    .setInputCols(['normalizedDocument'])\
    .setOutputCol('sentence') 

regexTokenizer = RegexTokenizer() \
    .setInputCols("sentence") \
    .setOutputCol("regexToken") \
    .setPattern(pattern) \
    .setPositionalMask(False)

pipeline = Pipeline().setStages([
    documentAssembler,
    documentNormalizer,
    sentenceDetector,
    regexTokenizer
])
text = """
<div id="theworldsgreatest" class='my-right my-hide-small my-wide toptext' style="font-family:'Segoe UI',Arial,sans-serif">
    THE WORLD'S LARGEST WEB DEVELOPER SITE
    <h1 style="font-size:300%;">THE WORLD'S LARGEST WEB DEVELOPER SITE</h1>
    <p style="font-size:160%;">Lorem Ipsum is simply dummy text of the printing and typesetting industry. Lorem Ipsum has been the industry's standard dummy text ever since the 1500s, when an unknown printer took a galley of type and scrambled it to make a type specimen book. It has survived not only five centuries, but also the leap into electronic typesetting, remaining essentially unchanged. It was popularised in the 1960s with the release of Letraset sheets containing Lorem Ipsum passages, and more recently with desktop publishing software like Aldus PageMaker including versions of Lorem Ipsum..</p>
</div>
</div>"""
data = spark.createDataFrame([[text]]).toDF("text")
data.show(10, False)
pipelineModel = pipeline.fit(data)
result = pipelineModel.transform(data)
#result.selectExpr("normalizedDocument").show(5, False)
result.selectExpr("sentence").show(5, False)

+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|text                                                                                                                      

In [78]:
import pyspark.sql.functions as F

result_df = result.select(F.explode('sentence.result').alias('regexToken')).toPandas()
result_df

regexToken
0  <div id="theworldsgreatest" class='my-right my...
1  ">the world's largest web developer site</h1> ...
2  ">lorem ipsum is simply dummy text of the prin...
3  lorem ipsum has been the industry's standard d...
4  it has survived not only five centuries, but a...
5  it was popularised in the 1960s with the relea...
6                                                  .
7                                 </p> </div> </div>

In [61]:
!wget http://setup.johnsnowlabs.com/colab.sh -O - | bash

--2022-03-30 09:11:35--  http://setup.johnsnowlabs.com/colab.sh
Resolving setup.johnsnowlabs.com (setup.johnsnowlabs.com)... 51.158.130.125
Connecting to setup.johnsnowlabs.com (setup.johnsnowlabs.com)|51.158.130.125|:80... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://setup.johnsnowlabs.com/colab.sh [following]
--2022-03-30 09:11:36--  https://setup.johnsnowlabs.com/colab.sh
Connecting to setup.johnsnowlabs.com (setup.johnsnowlabs.com)|51.158.130.125|:443... connected.
HTTP request sent, awaiting response... 302 Moved Temporarily
Location: https://raw.githubusercontent.com/JohnSnowLabs/spark-nlp/master/scripts/colab_setup.sh [following]
--2022-03-30 09:11:36--  https://raw.githubusercontent.com/JohnSnowLabs/spark-nlp/master/scripts/colab_setup.sh
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:44

In [79]:
pwd

'/home/yogender/Desktop/NN/data_engineer_case_study/data'